# Sustavi nelinearnih jednadžbi

---

__Problem.__ Nađimo rješenje $\xi=(\xi_1,\xi_2,\ldots,\xi_n)$ sustava od $n$ jednadžbi 

\begin{align*}
f_1(x)&=0,\\
f_2(x)&=0,\\
&\vdots \\
f_n(x)&=0,
\end{align*}

i $n$ nepoznanica $x=(x_1,x_2,\ldots,x_n)$. Uz oznaku $f=(f_1,f_2,\ldots,f_n)^T$, ovaj sustav možemo zapisati kao 

$$
f(x)=0.
$$

Opisat ćemo __Newtonovu metodu__ i tri __kvazi-Newtonove__ metode:

2. __Broydenovu__ metodu,
3. __Davidon-Fletcher-Powell__ metodu i 
3. __Broyden-Fletcher-Goldfarb-Schano__ metodu.

Sve metode, uz zadanu početnu aproksimaciju $x^{(0)}$,  generiraju niz točaka $x^{(n)}$ koji, uz određene uvjete, konvergira prema rješenju $\xi$. 

__Napomena.__ Opisi metoda i primjeri se nalaze u knjizi [Numerička matematika, poglavlje 4.4][RS04].

[RS04]: http://www.mathos.unios.hr/pim/Materijali/Num.pdf "R. Scitovski, 'Numerička matematika', Sveučilište u Osijeku, Osijek, 2004."

## Newtonova metoda

__Jacobijan__ ili __Jacobijeva matrica__ funkcija $f$ u točki $x$ je matrica prvih parcijalnih derivacija

$$
J(f,x)=\begin{bmatrix} \displaystyle\frac{\partial f_1(x)}{\partial x_1} & \displaystyle\frac{\partial f_1(x)}{\partial x_2} & \cdots &
\displaystyle\frac{\partial f_1(x)}{\partial x_n} \\
\displaystyle\frac{\partial f_2(x)}{\partial x_1} & \displaystyle\frac{\partial f_2(x)}{\partial x_2} & \cdots &
\displaystyle\frac{\partial f_2(x)}{\partial x_n} \\
\vdots & \vdots & \ddots & \vdots \\
\displaystyle\frac{\partial f_n(x)}{\partial x_1} & \displaystyle\frac{\partial f_n(x)}{\partial x_2} & \cdots &
\displaystyle\frac{\partial f_n(x)}{\partial x_n} 
\end{bmatrix}.
$$

Za zadanu početnu aproksimaciju $x^{(0)}$, računamo niz točaka

$$
x^{(k+1)}=x^{(k)}-s^{(k)}, \quad k=0,1,2,\ldots,
$$

gdje je $s^{(k)}$ rješenje sustava

$$
J\big(f,x^{(k)}\big)\cdot s=f\big(x^{(k)}\big).
$$

Za računanje Jacobijana koristimo paket [`ForwardDiff.jl`](http://www.juliadiff.org/ForwardDiff.jl/perf_diff.html#derivatives). Za crtanje funkcija koristimo paket `Plots.jl`.

In [1]:
using ForwardDiff
using Plots
plotly()
using LinearAlgebra

In [2]:
function Newton(f::Function,J::Function,x::Vector{T},ϵ::Float64=1e-10) where T
    iter=0
    s=ones(T,size(x))
    ξ=x
    while norm(s)>ϵ && iter<100
        s=J(x)\f(x)
        ξ=x-s
        iter+=1
        x=ξ
    end
    ξ,iter
end

Newton (generic function with 2 methods)

### Primjer 1

(Dennis i Schnabel, 1996) Rješenja sustava

\begin{align*}
2(x+y)^2+(x-y)^2-8&=0\\
5x^2+(y-3)^2-9&=0
\end{align*}

su točke $T_1=(1,1)$ i $T_2\approx(-1.18,1.59)$.

In [3]:
# Vektorska funkcija
f₁(x)=[2(x[1]+x[2])^2+(x[1]-x[2])^2-8,5*x[1]^2+(x[2]-3)^2-9]

f₁ (generic function with 1 method)

In [4]:
f₁((1.0,2))

2-element Array{Float64,1}:
 11.0
 -3.0

Nacrtajmo funkcije i konture kako bi mogli približno locirati nul-točke:

In [5]:
# Broj točaka
m=100
X=range(-2,stop=3,length=m)
Y=range(-2,stop=3,length=m)
# Prva aplikata
surface(X,Y,(x,y)->f₁([x,y])[1],xlabel="x",ylabel="y",colorbar=false)
# Druga aplikata
surface!(X,Y,(x,y)->f₁([x,y])[2],seriescolor=:blues)

<!DOCTYPE html>
 
 
 Plots.jl

In [6]:
# Odredimo rješenja pomoću kontura
contour(X,Y,(x,y)->f₁([x,y])[1],contour_labels=true)
contour!(X,Y,(x,y)->f₁([x,y])[2],contour_labels=true)

<!DOCTYPE html>
 
 
 Plots.jl

In [7]:
# Jasnija slika
contour!(clims=(0,0.01),xlabel="x",ylabel="y",colorbar=:none)

<!DOCTYPE html>
 
 
 Plots.jl

Vidimo da su nul-točke približno $T_1=(-1.2,1.5)$ i $T_2=(1,1)$. Štoviše, $T_2$ je točno jednaka $(1,1)$ (1 iteracija u trećem primjeru). Nadalje, metoda ne mora konvergirati (četvrti primjer).   

In [8]:
J₁(x)=ForwardDiff.jacobian(f₁,x)

J₁ (generic function with 1 method)

In [9]:
# Na primjer
J₁([1.0,2])

2×2 Array{Float64,2}:
 10.0  14.0
 10.0  -2.0

In [10]:
Newton(f₁,J₁,[-1.0,0.0]), Newton(f₁,J₁,[0.5,1.1]), 
Newton(f₁,J₁,[1.0,1.0]), Newton(f₁,J₁,[0.0,0.0])

(([-1.183467003241957, 1.5868371427229244], 8), ([1.0, 1.0], 6), ([1.0, 1.0], 1), ([NaN, NaN], 2))

### Primjer 2

(Dennis i Schnabel, 1996) Rješenja sustava

\begin{align*}
x_1^2-x_2^2-2&=0\\
e^{x_1-1}+x_2^3-2&=0
\end{align*}

su točke $T_1=(1,1)$ i $T_2\approx (-0.71,1.22)$ .

In [11]:
f₂(x)=[x[1]^2+x[2]^2-2,exp(x[1]-1)+x[2]^3-2]
contour(X,Y,(x,y)->f₁([x,y])[1],contour_labels=true)
contour!(X,Y,(x,y)->f₁([x,y])[2],contour_labels=true)
contour!(clims=(0,0.01),xlabel="x",ylabel="y",colorbar=:none)

<!DOCTYPE html>
 
 
 Plots.jl

In [12]:
J₂(x)=ForwardDiff.jacobian(f₂,x)
Newton(f₂,J₂,[-1.0,1]), Newton(f₂,J₂,[0.8,1.2])

(([-0.7137474114864426, 1.220886822189675], 5), ([1.0, 0.9999999999999999], 5))

### Primjer 3

(Dennis i Schnabel, 1996) Zadan je problem $f(x)=0$, gdje je

$$
f(x)=\begin{bmatrix}x_1 \\ x_2^2-x_2 \\ e^{x_3}-1 \end{bmatrix}.
$$

Točna rješenja su $T_1=(0,0,0)$ i $T_2=(0,-1,0)$. Izračunat ćemo nul-točke s nekoliko početnih aproksimacija.

In [13]:
f₃(x)=[x[1],x[2]^2+x[2],exp(x[3])-1]
J₃(x)=ForwardDiff.jacobian(f₃,x)

J₃ (generic function with 1 method)

In [14]:
Newton(f₃,J₃,[-1.0,1.0,0.0]),Newton(f₃,J₃,[1.0,1,1]),
Newton(f₃,J₃,[-1.0,1,-10]),Newton(f₃,J₃,[0.5,-1.5,0])

(([0.0, 0.0, 0.0], 7), ([0.0, 0.0, 7.783745890945912e-17], 7), ([0.0, 0.06666666666666665, NaN], 2), ([0.0, -1.0, 0.0], 6))

### Primjer 4

(Rosenbrock parabolic valley) Zadana je funkcija

$$
f(x)=100\,(x_2-x_1)^2+(1-x_1)^2.
$$

Tražimo moguće ekstreme funkcije, odnosno želimo riješiti jednadžbu

$$
\mathop{\mathrm{grad}} f(x)=0.
$$

In [15]:
f₄(x)=100(x[2]-x[1]^2)^2+(1-x[1])^2

f₄ (generic function with 1 method)

In [16]:
# Nacrtajmo funkciju koristeći X i Y iz Primjera 1
surface(X,Y,(x,y)->f₄([x,y]), seriescolor=:blues, xlabel="x", ylabel="y")

<!DOCTYPE html>
 
 
 Plots.jl

In [17]:
# Funkcija je zahtjevna u smislu određivanje ekstrema
g₄(x)=ForwardDiff.gradient(f₄,collect(x))
contour(X,Y,(x,y)->g₄([x,y])[1],contour_labels=true)
contour!(X,Y,(x,y)->g₄([x,y])[2],contour_labels=true)
contour!(clims=(-0.5,0.5),xlabel="x",ylabel="y",colorbar=:none)

<!DOCTYPE html>
 
 
 Plots.jl

Iz kontura vidimo da je primjer numerički zahtjevan, dok analitički lako vidimo da je jedina nul-točka $x_1=(1,1)$.

U ovom primjeru funkcija je zadana kao gradijent skalarne funkcije pa Jacobijevu matricu računamo korištenjem funkcije `FowardDiff.hessian()` koja računa aproksimaciju matrice drugih parcijalnih derivacija polazne funkcije. 

In [18]:
Newton(g₄,x->ForwardDiff.hessian(f₄,x),[-1.0,2.0])

([1.0, 1.0], 7)

### Primjer 5

Zadana je fukcija

$$
f(x)=\sum_{i=1}^{11} \bigg(x_3 \cdot \exp\bigg(-\frac{(t_i-x_1)^2}{x_2}\bigg)-y_i\bigg)^2,
$$

gdje su brojevi $(t_i,y_i)$ zadani tablicom:

| $i$ | 1 | 2 | 3 | 4 | 5 | 6 | 7 | 8 | 9 |10 | 11 |
| --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- |
| $t_i$ | 0 | 1 | 2 | 3 | 4 | 5 | 6 | 7 | 8 | 9 |10 | 
| $y_i$ | 0.001 | .01 | .04 | .12 | .21 | .25 | .21 | .12 | .04 | .01 | .001 |

Želimo riješiti jednadžbu 

$$
\mathop{\mathrm{grad}} f(x)=0.
$$


Za razliku od prethodnih zadataka, gdje je kondicija 

$$\kappa(J)=O(10)$$ 

u zadacima (a), (b) i (c) i 

$$\kappa(J)=O(1000)$$ 

u zadatku (d), u ovom zadatku je 

$$\kappa(J)>O(10^6)$$ 

pa je metoda netočna i ne konvergira prema točnom rješenju $x=(4.93,2.62,0.28)$.

In [19]:
t=collect(0:10)
y=[0.001,0.01,0.04,0.12,0.21,0.25,0.21,0.12,0.04,0.01,0.001]
f₅(x)=sum([( x[3]*exp(-((t[i]-x[1])^2/x[2]))-y[1])^2 for i=1:11])

f₅ (generic function with 1 method)

In [20]:
# Početna točka je vrlo blizu rješenja
x₀=[4.9,2.63,0.28]
f₅(x₀)
g₅(x)=ForwardDiff.gradient(f₅,x)
J₅(x)=ForwardDiff.hessian(f₅,x)
f₅(x₀), g₅(x₀), cond(J₅(x₀))

(0.15775257532454934, [2.715533686349289e-6, 0.029985961264699698, 1.1324744072032398], 173703.69351181446)

In [21]:
x₅,iter₅=Newton(g₅,J₅,x₀,1e-8)

([6.502441314556678, 0.0024508472251587193, -1.608880054863579e-7], 100)

In [22]:
g₅(x₅)

3-element Array{Float64,1}:
  1.523560685122021e-51
  2.043007334415462e-49
 -3.073712817083802e-47

In [23]:
Newton(g₅,J₅,[4.9,2.62,0.28],1e-8)

([NaN, NaN, NaN], 13)

## Broydenova metoda

Za odabranu početnu aproksimaciju $x_0$ i matricu $B_0$, za $k=0,1,2,\ldots$, računamo redom:

\begin{align*}
B_k \cdot s_k & = -f(x_k) \quad \textrm{(sustav)}\\
x_{k+1}&=x_{k}+s_k\\
y_k&=f(x_{k+1})-f(x_{k})\\
B_{k+1}&=B_k+\frac{(y_k-B_ks_k)s_k^T}{s_k\cdot s_k}
\end{align*}

Na ovaj način izbjegavamo računanje Jacobijeve matrice u svakom koraku.
Možemo uzeti $B_0=J(x_0)$, ali i neku drugu matricu.

In [24]:
function Broyden(f::Function,B::Matrix,x::Vector{T},ϵ::Float64=1e-10) where T
    iter=0
    s=ones(T,length(x))
    ξ=x
    while norm(s)>ϵ && iter<100
        s=-(B\f(x))
        ξ=x+s
        y=f(ξ)-f(x)
        B=B+(y-B*s)*(s/(s⋅s))'
        x=ξ
        iter+=1
    end
    ξ,iter
end

Broyden (generic function with 2 methods)

In [25]:
# Primjer 1
Broyden(f₁,J₁([-1.0,0.0]),[-1.0,0.0]), 
Broyden(f₁,J₁([1.0,1.5]),[1.0,1.5])

(([-1.1834670032419574, 1.586837142722924], 12), ([0.9999999999999917, 0.9999999999999969], 7))

In [26]:
# Objasnite ponašanje metode kada za početnu matricu uzmemo jediničnu matricu!
eye(n)=Matrix{Float64}(I,n,n)
Broyden(f₁,eye(2),[-1.0,0.0]), Broyden(f₁,eye(2),[1.0,1.5]),
Broyden(f₁,eye(2),[-1,1.5])

(([-0.035639080851908034, -2.5316602095531238], 100), ([0.9160215171939703, -3.045472257505457], 100), ([-1.183467003241957, 1.5868371427229242], 14))

In [27]:
# Primjer 2
x0=[-1.0,1]
x1=[0.8,1.2]
Broyden(f₂,J₂([-1.0,1]),[-1.0,1]), Broyden(f₂,J₂([0.8,1.2]),[0.8,1.2])

(([-0.7137474114864439, 1.2208868221896745], 9), ([1.0000000000000002, 0.9999999999999999], 9))

In [28]:
# Primjer 3
Broyden(f₃,J₃([-1.0,1,0]),[-1.0,1,0]), Broyden(f₃,J₃([0.5,-1.5,0]),[0.5,-1.5,0])

(([0.0, 5.965361234900634e-26, 0.0], 9), ([0.0, -1.0, 0.0], 8))

In [29]:
# Primjer 4
Broyden(g₄,(x->ForwardDiff.hessian(f₄,x))([-1.0,2]),[-1.0,2]), # ali
Broyden(g₄,(x->ForwardDiff.hessian(f₄,x))([1,2.0]),[-1.0,2]),
Broyden(g₄,(x->ForwardDiff.hessian(f₄,x))([0.8,0.5]),[0.8,0.5])

(([0.8340640648114012, 0.6950420895200371], 100), ([1.0000000000000009, 1.0000000000000018], 4), ([1.0000000000000073, 1.0000000000000144], 29))

In [30]:
# Primjer 5
x₀=[4.9,2.6,0.2]
x₅,iter₅=Broyden(g₅,(x->ForwardDiff.hessian(f₅,x))(x₀),x₀)

([18.90031560465981, 1.3239864192858994, 0.06655170834063737], 6)

In [31]:
g₅(x₅)

3-element Array{Float64,1}:
  1.8552699559685368e-29
 -6.235898383995474e-29
 -2.0734616070093272e-29

## Davidon-Fletcher-Powell (DFP) metoda

DFP je optimizacijska metoda koja traži točke ekstrema funkcije 
$F:\mathbb{R}^n \to \mathbb{R}$, u kojem slučaju je $f(x)=\mathop{\mathrm{grad}}F(x)$.

Za odabranu početnu aproksimaciju $x_0$ i matricu $H_0$, za $k=0,1,2,\ldots$, računamo redom:

\begin{align*}
s_k&=-H_k f(x_k)\\
\beta_k&=\mathop{\mathrm{arg\ min}}_\beta F(x_{k}+\beta s_k) \\
s_k&=\beta_k s_k\\
x_{k+1}&=x_{k}+s_k \\
y_k&=f(x_{k+1})-f(x_{k})\\
H_{k+1}&=H_k+ \frac{s_k s_k^T}{y_k\cdot s_k}-\frac{H_k y_k y_k^T H_k}{y_k\cdot (H_k y_k)}.
\end{align*}

Za matricu $H_0$ možemo uzeti jediničnu matricu, a za izvršavanje iteracije nije potrebno rješavati sustav linearnih jednadžbi, već se sva ažuriranja vrše s $O(n^2)$ operacija.

Jednodimenzionalnu minimizaciju po pravcu $x_{k}+\beta s_k$ računamo tako što metodom bisekcije nađemo nul-točke usmjerene derivacije.

In [32]:
function Bisekcija(f::Function,a::T,b::T,ϵ::Float64=1e-10) where T
    fa=f(a)
    fb=f(b)
    x=T
    fx=T
    if fa*fb>zero(T)
        # return "Incorrect interval"
        if abs(fa)>abs(fb)
            return b,fb,0
        else
            return a,fa,0
        end
    end
    iter=0
    while b-a>ϵ && iter<1000
        x=(b+a)/2.0
        fx=f(x)
        if fa*fx<zero(T)
            b=x
            fb=fx
        else
            a=x
            fa=fx
        end
        iter+=1
        # @show x,fx
    end
    x,fx,iter
end

Bisekcija (generic function with 2 methods)

In [33]:
function DFP(f::Function,H::Matrix,x::Vector{T},ϵ::Float64=1e-10) where T
    iter=0
    s=ones(T,length(x))
    ξ=x
    while norm(s)>ϵ && iter<50
        s=-H*f(x)
        s0=s/norm(s)
        F(ζ)=f(x+ζ*s)⋅s0
        β,fx,iterb=Bisekcija(F,0.0,1.0,10*eps())
        s*=β
        ξ=x+s
        y=f(ξ)-f(x)
        z=H*y
        H=H+(s/(y⋅s))*s'-(z/(y⋅z))*z'
        x=ξ
        iter+=1
    end
    ξ,iter
end

DFP (generic function with 2 methods)

__Primjer.__ Nađimo točku ekstrema funkcije 

$$
f(x,y)=(x+2y-7)^2+(2x+y-5)^2.
$$

Funkcija ima minimum u točki $(1,3)$.

In [34]:
f₆(x) = (x[1] + 2*x[2]-7)^2 + (2*x[1] + x[2]-5)^2

f₆ (generic function with 1 method)

In [35]:
f₆([1,2])

5

In [36]:
g₆(x)=ForwardDiff.gradient(f₆,x)

g₆ (generic function with 1 method)

In [37]:
DFP(g₆,eye(2),[0.8,2.7],eps())

([1.0, 3.0], 4)

In [38]:
# Primjer 4
DFP(g₄,eye(2),[0.9,1.1])

([1.0000000000000002, 1.0000000000000004], 9)

In [39]:
# Primjer 5
DFP(g₅,eye(3),[4.9,2.6,0.2])

([4.896114590499003, 46.19785538124626, 0.0015891269930557736], 25)

## Broyden-Fletcher-Goldfarb-Schano (BFGS) metoda

BFGS je optimizacijska metoda koja uspješno traži točke ekstrema funkcije 
$F:\mathbb{R}^n \to \mathbb{R}$, u kojem slučaju je $f(x)=\mathop{\mathrm{grad}}F(x)$.

Metoda je slična DFP metodi, s nešto boljim svojstvima konvergencije.

Neka je zadana funkcija $F:\mathbb{R}^n \to \mathbb{R}$, čiji minimum tražimo, i neka je 
$f(x)=\mathop{\mathrm{grad}} F(x)$.

Za odabranu početnu aproksimaciju $x_0$ i matricu $H_0$, za $k=0,1,2,\ldots$, računamo redom:

\begin{align*}
s_k&=-H_k f(x_k)\\
\beta_k&=\mathop{\mathrm{arg\ min}}F(x_{k}+\beta_k s_k) \\
s_k&=\beta_k s_k\\
x_{k+1}&=x_{k}+s_k \\
y_k&=f(x_{k+1})-f(x_{k})\\
H_{k+1}&=\bigg(I-\frac{s_k y_k^T}{y_k\cdot s_k}\bigg)H_k
\bigg( I-\frac{y_k s_k^T}{y_k\cdot s_k}\bigg)+\frac{s_k s_k^T}{y_k\cdot s_k}.
\end{align*}

Za matricu $H_0$ možemo uzeti jediničnu matricu, a za izvršavanje iteracije nije potrebno rješavati sustav linearnih jednadžbi, već se sva ažuriranja vrše s $O(n^2)$ operacija.

Jednodimenzionalnu minimizaciju po pravcu $x_{k}+\beta s_k$ računamo tako što metodom bisekcije tražimo nul-točke usmjerene derivacije.

In [40]:
function BFGS(f::Function,H::Matrix,x::Vector{T},ϵ::Float64=1e-10) where T
    iter=0
    s=ones(T,length(x))
    ξ=x
    while norm(s)>ϵ && iter<50
        s=-H*f(x)
        s0=s/norm(s)
        F(ζ)=f(x+ζ*s)⋅s0
        β,fx,iterb=Bisekcija(F,0.0,1.0,10*eps())
        s*=β
        ξ=x+s
        y=f(ξ)-f(x)
        z=H*y
        α=y⋅s
        s1=s/α
        H=H-s1*z'-z*s1'+s1*(y⋅z)*s1'+s1*s'
        x=ξ
        iter+=1
    end
    ξ,iter
end

BFGS (generic function with 2 methods)

In [41]:
BFGS(g₆,eye(2),[0.8,2.7],eps())

([1.0, 3.0], 4)

In [42]:
# Primjer 4
BFGS(g₄,eye(2),[0.9,1.1])

([1.0, 1.0000000000000002], 9)

In [43]:
# Primjer 5
BFGS(g₅,eye(3),[4.9,2.6,0.2])

([2.0890765836488763, 31226.563051597408, 0.0010005592043970898], 50)

## Julia paketi

Prethodni programi su jednostavne ilustrativne implementacije navedenih algoritama.
Julia ima paket [NLsolve.jl](https://github.com/JuliaNLSolvers/NLsolve.jl) za rješavanje sustava nelineranih jednadžbi i paket [Optim.jl](https://github.com/JuliaNLSolvers/Optim.jl) za nelinearnu optimizaciju.

In [44]:
using NLsolve

In [45]:
# Primjer 1
function f₁!(fvec,x)
    fvec[1] = 2(x[1]+x[2])^2+(x[1]-x[2])^2-8
    fvec[2] = 5*x[1]^2+(x[2]-3)^2-9
end

f₁! (generic function with 1 method)

In [46]:
nlsolve(f₁!,[-1.0,0])

Results of Nonlinear Solver Algorithm
 * Algorithm: Trust-region with dogleg and autoscaling
 * Starting Point: [-1.0, 0.0]
 * Zero: [-1.1834670032425283, 1.5868371427230779]
 * Inf-norm of residuals: 0.000000
 * Iterations: 5
 * Convergence: true
   * |x - x'| < 0.0e+00: false
   * |f(x)| < 1.0e-08: true
 * Function Calls (f): 6
 * Jacobian Calls (df/dx): 6

In [47]:
nlsolve(f₁!,[0.5,1.1])

Results of Nonlinear Solver Algorithm
 * Algorithm: Trust-region with dogleg and autoscaling
 * Starting Point: [0.5, 1.1]
 * Zero: [1.0000000000000002, 1.0000000000000002]
 * Inf-norm of residuals: 0.000000
 * Iterations: 5
 * Convergence: true
   * |x - x'| < 0.0e+00: false
   * |f(x)| < 1.0e-08: true
 * Function Calls (f): 6
 * Jacobian Calls (df/dx): 6

In [48]:
# Primjer 2
function f₂!(fvec,x)
    fvec[1] = x[1]^2+x[2]^2-2
    fvec[2] = exp(x[1]-1)+x[2]^3-2
end
nlsolve(f₂!,[-1.0,1]), nlsolve(f₂!,[0.8,1.2])

(Results of Nonlinear Solver Algorithm
 * Algorithm: Trust-region with dogleg and autoscaling
 * Starting Point: [-1.0, 1.0]
 * Zero: [-0.7137474114758742, 1.2208868222037403]
 * Inf-norm of residuals: 0.000000
 * Iterations: 4
 * Convergence: true
   * |x - x'| < 0.0e+00: false
   * |f(x)| < 1.0e-08: true
 * Function Calls (f): 5
 * Jacobian Calls (df/dx): 5, Results of Nonlinear Solver Algorithm
 * Algorithm: Trust-region with dogleg and autoscaling
 * Starting Point: [0.8, 1.2]
 * Zero: [0.9999999999940328, 1.0000000000115203]
 * Inf-norm of residuals: 0.000000
 * Iterations: 4
 * Convergence: true
   * |x - x'| < 0.0e+00: false
   * |f(x)| < 1.0e-08: true
 * Function Calls (f): 5
 * Jacobian Calls (df/dx): 5)

In [49]:
# Primjer 3
function f₃!(fvec,x)
    fvec[1] = x[1]
    fvec[2] = x[2]^2+x[2]
    fvec[3] = exp(x[3])-1
end
nlsolve(f₃!,[-1.0,1.0,0.0]), nlsolve(f₃!,[1.0,1,1]),
nlsolve(f₃!,[-1.0,1,-10]), nlsolve(f₃!,[0.5,-1.5,0])

(Results of Nonlinear Solver Algorithm
 * Algorithm: Trust-region with dogleg and autoscaling
 * Starting Point: [-1.0, 1.0, 0.0]
 * Zero: [0.0, 2.3283064364709337e-10, 0.0]
 * Inf-norm of residuals: 0.000000
 * Iterations: 5
 * Convergence: true
   * |x - x'| < 0.0e+00: false
   * |f(x)| < 1.0e-08: true
 * Function Calls (f): 6
 * Jacobian Calls (df/dx): 6, Results of Nonlinear Solver Algorithm
 * Algorithm: Trust-region with dogleg and autoscaling
 * Starting Point: [1.0, 1.0, 1.0]
 * Zero: [0.0, 2.3283064364709337e-10, 1.223235687436471e-12]
 * Inf-norm of residuals: 0.000000
 * Iterations: 5
 * Convergence: true
   * |x - x'| < 0.0e+00: false
   * |f(x)| < 1.0e-08: true
 * Function Calls (f): 6
 * Jacobian Calls (df/dx): 6, Results of Nonlinear Solver Algorithm
 * Algorithm: Trust-region with dogleg and autoscaling
 * Starting Point: [-1.0, 1.0, -10.0]
 * Zero: [0.0, 4.9978109751571114e-11, 8.131707812509303e-17]
 * Inf-norm of residuals: 0.000000
 * Iterations: 20
 * Convergence: 

In [50]:
using Optim

In [51]:
# Primjer 4
optimize(f₄,[-1.0,2],Optim.BFGS())

 * Status: success

 * Candidate solution
    Final objective value:     5.375030e-17

 * Found with
    Algorithm:     BFGS

 * Convergence measures
    |x - x'|               = 5.13e-09 ≰ 0.0e+00
    |x - x'|/|x'|          = 5.13e-09 ≰ 0.0e+00
    |f(x) - f(x')|         = 9.67e-17 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 1.80e+00 ≰ 0.0e+00
    |g(x)|                 = 2.10e-11 ≤ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    35
    f(x) calls:    102
    ∇f(x) calls:   102


In [52]:
# Primjer 5 - opet ne konvergira prema rješenju
optimize(f₅,[4.9,2.6,0.2],Optim.BFGS())

 * Status: success

 * Candidate solution
    Final objective value:     3.572548e-12

 * Found with
    Algorithm:     BFGS

 * Convergence measures
    |x - x'|               = 1.87e+05 ≰ 0.0e+00
    |x - x'|/|x'|          = 8.70e-02 ≰ 0.0e+00
    |f(x) - f(x')|         = 6.03e-16 ≰ 0.0e+00
    |f(x) - f(x')|/|f(x')| = 1.69e-04 ≰ 0.0e+00
    |g(x)|                 = 9.69e-09 ≤ 1.0e-08

 * Work counters
    Seconds run:   0  (vs limit Inf)
    Iterations:    41
    f(x) calls:    137
    ∇f(x) calls:   137
